# Glauber Monte Carlo calculation

In [ ]:
# clear all variables
%reset -f

import numpy as np
import matplotlib.pyplot as plt
import itertools
import scipy as sp
import pandas as pd

## A helper function to get random numbers from a user-defined distribution:

In [ ]:
def get_random(f, xmin, xmax, n_samples):
    """Generate n_samples random numbers within range [xmin, xmax] 
    from arbitrary continuous function f
    using inverse transform sampling 
    """ 
    
    # number of points for which we evaluate F(x)
    nbins = 10000
    
    # indefinite integral F(x), normalize to unity at xmax 
    x = np.linspace(xmin, xmax, nbins+1)
    F = sp.integrate.cumtrapz(f(x), x, initial=0)
    F = F / F[-1]
    
    # interpolate F^{-1} and evaluate it for 
    # uniformly distributed rv's in [0,1[
    inv_F = sp.interpolate.interp1d(F, x, kind="quadratic")
    r = np.random.rand(n_samples)
    return inv_F(r)

##  Define nuclear density distributions

In [ ]:
# dN/dr distribution for Pb
def dndr_lead(r):
    '''nucleon density distribution of Pb (arbitrary normalization)'''
    R = 6.68 # fm
    a = 0.54 # fm
    return r**2/(1 + np.exp((r-R)/a))

## Parameters: #events, nuclear mass numbers, nucleon-nucleon cross section

In [ ]:
n_events = 1000
A1 = 208 # lead
A2 = 208 # lead
sigma_nn_inel_fm2 = 64. / 10;  # 1 mb = 0.1 fm^2 

# Define spatial positions of all nucleons in nucleus 1 and nucleus 2 for all events

Doing this beforehand requires more memory but is faster.

In [ ]:
bmax = 18. # fm

# draw values from impact parameter distribution dN/db = 2 pi b using the inverse transform method
z = np.random.uniform(0., 1., n_events)
b = bmax * np.sqrt(z)
impact_pars = b.reshape(-1, 1) # this shape (impact parameters as column vector) is needed below 

rmax = 8 # maximum radius in fm fm 
R1 = get_random(dndr_lead, 0., rmax, A1 * n_events)
R2 = get_random(dndr_lead, 0., rmax, A2 * n_events)

R1 = R1.reshape((n_events, A1))
R2 = R2.reshape((n_events, A2))

phi1 = np.random.uniform(0., 2*np.pi, (n_events, A1))
theta1 = np.arccos(np.random.uniform(-1., 1., (n_events, A1)))
x1 = R1 * np.sin(theta1) * np.cos(phi1) + impact_pars/2.
y1 = R1 * np.sin(theta1) * np.sin(phi1)
z1 = R1 * np.cos(theta1)

phi2 = np.random.uniform(0., 2*np.pi, (n_events, A2))
theta2 = np.arccos(np.random.uniform(-1., 1., (n_events, A2)))
x2 = R2 * np.sin(theta2) * np.cos(phi2) - impact_pars/2.
y2 = R2 * np.sin(theta2) * np.sin(phi2)
z2 = R2 * np.cos(theta2)


## The main event loop

In [ ]:
from ipywidgets import IntProgress
from IPython.display import display

progress_bar = IntProgress(min=0, max=n_events, description='Events:') # instantiate the bar
display(progress_bar) # display the bar

# array to store Npart and Ncoll values for each event
npart = np.zeros(n_events)  # array of Npart values (initialized with zeros)
ncoll = np.zeros(n_events)  # array of Ncoll values (initialized with zeros)

for i_event in range(n_events):
    
    if i_event % 10 == 0: progress_bar.value += 10
        
    # array to store number of collisions for each nucleon in this event (for nucleus 1 and nucleus 2)
    nc1 = np.zeros(A1)
    nc2 = np.zeros(A2)
    
    # list with nucleon indicees
    in1 = range(A1)
    in2 = range(A2)
    
    # consider all pairs (nucleon 1 from nucleus 1, nucleon 2 from nucleus 2)
    for (i1, i2) in itertools.product(in1, in2):

        # calculate (squared) distance of the two nucleons in the transverse plane

        # add code here  
        d_squared = ...

        # check if two nucleon are close enough 
            
        # add code here
        if ...:
            ncoll[i_event] += 1
            if (nc1[i1] == 0): npart[i_event] += 1
            if (nc2[i2] == 0): npart[i_event] += 1
            
            nc1[i1] += 1
            nc2[i2] += 1

## Plot impact parameter distribution

In [ ]:
plt.hist(b, bins=50, range=(0., bmax), alpha=0.5, histtype='step', label='all')
# plt.hist(impact_pars_inel, bins=50, range=(0., 15.), histtype='step', label='inelastic')
plt.hist(b[ncoll > 0], bins=50, range=(0., bmax), histtype='step', label='inelastic')
plt.xlabel('impact parameter $b$ (fm)', size=18)
plt.ylabel('# events', size=18)
plt.legend(fontsize=18, loc='upper left')
plt.show()

## Scatter plot of $N_\mathrm{part}$ as a function of the impact parameter

In [ ]:
# add code here

## Mean $N_\mathrm{part}$ and $N_\mathrm{coll}$ for the 10% most central inelastic collisions

In [ ]:
bmax_0_10 = np.quantile(b[ncoll > 0], 0.1)
mask = (ncoll > 0) & (b < bmax_0_10)

# add code here


## Total inelastic cross section

The total inelastic cross section is given by 
$$\sigma_\mathrm{inel} = \int_{0}^{b_\mathrm{max}} \frac{d \sigma_\mathrm{inel}}{db} \, db.$$
From the Glauber Monte Carlo calculation we have $dn_\mathrm{inel}/db$ and so we just need to determine the proper normalization $N$:
$$\sigma_\mathrm{inel} = N \int_{0}^{b_\mathrm{max}} \frac{d n_\mathrm{inel}}{db} \, db = N \cdot n_\mathrm{inel}.$$
For the impact parameter distribution of the generated events in the interval $0$-$b_\mathrm{max}$ we know the geometric cross section
$$\sigma_\mathrm{geo} = \pi b_\mathrm{max}^2 = N \int_{0}^{b_\mathrm{max}} \frac{d n_\mathrm{gen}}{db} \, db  = N \cdot n_\mathrm{gen} \quad \Rightarrow \quad N = \frac{\pi b_\mathrm{max}^2}{n_\mathrm{gen}}.$$
This then gives
$$ \sigma_\mathrm{inel} = \frac{n_\mathrm{inel}}{n_\mathrm{gen}}\pi b_\mathrm{max}^2$$

In [ ]:
# add code here